In [1]:
%load_ext autoreload
%autoreload 1

In [1]:
import os
import tempfile
from pathlib import PosixPath

import gymnasium
import numpy as np

import minetest

BOAD_CONFIG_TEXT = """STARVE_1_MUL=20
STARVE_2_MUL=20
ALLOW_NIGHT=0
"""

game = "boad" # "devtest" # 

repo_root = PosixPath('/home/eric/minetest') # Path(globals()['_dh'][0]).parent.parent
temp_dir = tempfile.mkdtemp(prefix="minetest_")

base_dir = os.environ["CONDA_PREFIX"] # if game == "devtest" else os.path.join(os.path.abspath(''), ".pixi/envs/default")
game_dir = os.path.join(base_dir, "share/minetest/games", game)
print(game_dir)

# install devtest game if needed
if not os.path.exists(game_dir):
    os.makedirs(os.path.dirname(game_dir), exist_ok=True)
    os.symlink(os.path.realpath(os.path.join(repo_root, "games", game)), game_dir)

if game == "boad":
    config = os.path.join(game_dir, "config.lua")
    with open(config, "w") as f:
        f.write(BOAD_CONFIG_TEXT)

# use minetest from repo if needed
minetest_executable = os.path.join(base_dir, "bin/minetest")
if not os.path.exists(minetest_executable):
    minetest_executable = os.path.join(repo_root, "bin/minetest")
print(f"Using minetest executable: {minetest_executable}")

env = minetest.MinetestEnv(
    executable=minetest_executable,
    artifact_dir=os.path.join(temp_dir, "artifacts"),
    game_dir=game_dir,
)
video_dir = os.path.join(temp_dir, "video")
empty_action = {"KEYS": np.ndarray(0), "MOUSE": [0, 0]}
with gymnasium.wrappers.RecordVideo(env, video_dir) as env:
    env.reset()
    for i in range(1000):
        action = env.action_space.sample() if i % 10 == 0 else empty_action
        observation, reward, done, truncated, info = env.step(action)
        if done: break


/home/eric/minetest/python/examples/.pixi/envs/default/share/minetest/games/boad
Using minetest executable: /home/eric/minetest/python/examples/.pixi/envs/default/bin/minetest


kj/filesystem-disk-unix.c++:1703: warning: PWD environment variable doesn't match current directory; pwd = /home/eric


KeyboardInterrupt: 

## Note
If you see `Irrlicht: GL_INVALID_OPERATION` on the recording, this will not happen in a Release build.
We see that with SDL2 rendering but not X11, so it's probably an upstream bug.
Doesn't seem to break anything though.

In [3]:
import io
import base64
from IPython.display import HTML

video = io.open(os.path.join(video_dir, os.listdir(video_dir)[-1]), "r+b").read()
encoded = base64.b64encode(video)
HTML(data='''
    <video width="360" height="auto" alt="test" controls><source src="data:video/mp4;base64,{0}" type="video/mp4" /></video>'''
.format(encoded.decode("ascii")))